# 🧬 Scaling In-Silico Perturbation Inference with Geneformer

This notebook evaluates batching to speed up Geneformer in-silico perturbation inference while maintaining baseline-equivalent embeddings.

### Overview

- **Task:** Scale in-silico perturbation inference for Geneformer
- **Baseline:** Naive per-cell inference loop
- **Optimization:** Batched inference
- **Metrics:** Runtime, throughput, embedding similarity
- **Outcome:** Significant speedup over baseline with numerically equivalent output

## 1) Setup: Installations & Imports
Install the required dependencies and import all libraries used throughout the notebook. Specific versions are pinned where needed to ensure compatibility with the Helical Geneformer examples.

In [ ]:
!pip -q install --upgrade pip

# Explicit torch install to guarantee CUDA-enabled inference
!pip -q install --no-cache-dir \
  torch==2.5.1 torchvision==0.20.1 torchaudio==2.5.1 \
  --index-url https://download.pytorch.org/whl/cu121

# Install helical without deps
!pip -q install --no-deps helical

# Manually install only the deps we actually need
!pip -q install \
  "datasets<4.0.0" \
  transformers anndata hydra-core requests_cache scanpy

In [ ]:
# Standard library
import os
import time
import subprocess
import textwrap
import urllib.request

# System / profiling
import psutil

# Scientific Python stack
import numpy as np
import pandas as pd
import scipy.sparse as sp
import matplotlib.pyplot as plt

# ML frameworks
import torch
from datasets import load_dataset
import anndata as ad

# Helical
from helical.models.geneformer import Geneformer, GeneformerConfig
from helical.utils import get_anndata_from_hf_dataset


## 2) Dataset Loading & Preparation
 Loads a small subset of the human yolk sac single-cell dataset provided by Helical. This dataset is used consistently throughout the notebook to ensure fair comparison across inference strategies.

In [ ]:
# Load the data set
def load_yolksac_subset(n_cells: int = 500, split: str = "train", seed: int = 42):
    """Load a reproducible subset of the yolk sac dataset as AnnData."""
    ds = load_dataset(
        "helical-ai/yolksac_human",
        trust_remote_code=True,
        download_mode="reuse_cache_if_exists",
    )
    ds = ds.shuffle(seed=seed)
    adata = get_anndata_from_hf_dataset(ds[split])
    return adata[:n_cells].copy()

# Working dataset used throughout the notebook
N_CELLS = 500
adata = load_yolksac_subset(n_cells=N_CELLS)

print("Dataset summary")
print("----------------")
print("Cells:", adata.n_obs)
print("Genes:", adata.n_vars)
print("X type:", type(adata.X))

The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(

2026-01-13 16:00:52,566 - WARNING:py.warnings:/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(



README.md: 0.00B [00:00, ?B/s]

yolksac_human.py: 0.00B [00:00, ?B/s]

./data/17_04_24_YolkSacRaw_F158_WE_annot(…):   0%|          | 0.00/553M [00:00<?, ?B/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

  return dispatch(args[0].__class__)(*args, **kw)

2026-01-13 16:02:37,035 - WARNING:py.warnings:/usr/lib/python3.12/functools.py:912: ImplicitModificationWarning: Transforming to str index.
  return dispatch(args[0].__class__)(*args, **kw)



Dataset summary
----------------
Cells: 500
Genes: 37318
X type: <class 'scipy.sparse._csr.csr_matrix'>


## 3) In-Silico Perturbation Generation
Generate single-gene in-silico perturbations from one base cell. Each perturbation modifies exactly one gene (e.g., knockout), producing a batch of perturbed cells suitable for batched inference.

In [ ]:
def pick_expressed_genes(
    adata,
    cell_idx: int,
    n_genes: int = 100,
    seed: int = 0,
) -> np.ndarray:
    """
    Select a random subset of expressed genes from a single cell.
    """
    rng = np.random.default_rng(seed)

    cell_expression = adata.X[cell_idx]

    # Identify genes with non-zero expression
    if sp.issparse(cell_expression):
        expressed_gene_indices = cell_expression.indices
    else:
        expressed_gene_indices = np.where(cell_expression > 0)[0]

    if len(expressed_gene_indices) == 0:
        raise ValueError("Selected cell has no expressed genes.")

    return rng.choice(
        expressed_gene_indices,
        size=min(n_genes, len(expressed_gene_indices)),
        replace=False,
    )


def generate_single_cell_perturbations(
    adata: ad.AnnData,
    cell_idx: int,
    gene_indices: np.ndarray,
    mode: str = "knockout",
    overexpress_factor: float = 2.0,
) -> ad.AnnData:
    """
    Generate single-gene perturbations from one base cell.
    """
    base_row = adata.X[cell_idx].copy()

    if sp.issparse(base_row):
        base_row = base_row.toarray().ravel()

    perturbed_rows = []
    obs_records = []

    for g in gene_indices:
        row = base_row.copy()

        if mode == "knockout":
            row[g] = 0
        elif mode == "overexpress":
            row[g] = row[g] * overexpress_factor if row[g] != 0 else overexpress_factor
        else:
            raise ValueError("mode must be 'knockout' or 'overexpress'")

        perturbed_rows.append(row)
        obs_records.append(
            {
                "base_cell_idx": cell_idx,
                "perturbation": mode,
                "gene_idx": int(g),
                "gene_name": adata.var_names[g],
            }
        )

    X = np.vstack(perturbed_rows)
    return ad.AnnData(X=X, obs=pd.DataFrame(obs_records), var=adata.var.copy())

Each row in the resulting AnnData object represents a modified copy of the same base cell, where exactly one gene has been perturbed.


In [ ]:
BASE_CELL_IDX = 0
N_PERTURBATIONS = 200
PERTURB_MODE = "knockout"
SEED = 42

gene_idxs = pick_expressed_genes(
    adata,
    cell_idx=BASE_CELL_IDX,
    n_genes=N_PERTURBATIONS,
    seed=SEED,
)

perturbed_adata = generate_single_cell_perturbations(
    adata,
    cell_idx=BASE_CELL_IDX,
    gene_indices=gene_idxs,
    mode=PERTURB_MODE,
)

print("Base cell index:", BASE_CELL_IDX)
print("Number of perturbations:", perturbed_adata.n_obs)
print("Number of genes:", perturbed_adata.n_vars)
print("X shape:", perturbed_adata.X.shape)
print("X type:", type(perturbed_adata.X))

perturbed_adata.obs.head()

  return dispatch(args[0].__class__)(*args, **kw)

2026-01-13 16:02:38,651 - WARNING:py.warnings:/usr/lib/python3.12/functools.py:912: ImplicitModificationWarning: Transforming to str index.
  return dispatch(args[0].__class__)(*args, **kw)



Base cell index: 0
Number of perturbations: 200
Number of genes: 37318
X shape: (200, 37318)
X type: <class 'numpy.ndarray'>


base_cell_idx perturbation  gene_idx gene_name
0              0     knockout     17525  HIST1H1C
1              0     knockout     22532   MT-ND4L
2              0     knockout     21868      MED6
3              0     knockout     10147     BLVRB
4              0     knockout     10117       BID

In [ ]:
# Example of overexpression (illustrative, not used for benchmarking)
perturbed_adata_oe = generate_single_cell_perturbations(
    adata,
    cell_idx=BASE_CELL_IDX,
    gene_indices=gene_idxs,
    mode="overexpress",
    overexpress_factor=2.0,
)
perturbed_adata_oe.obs.head()

  return dispatch(args[0].__class__)(*args, **kw)

2026-01-13 16:02:38,711 - WARNING:py.warnings:/usr/lib/python3.12/functools.py:912: ImplicitModificationWarning: Transforming to str index.
  return dispatch(args[0].__class__)(*args, **kw)



base_cell_idx perturbation  gene_idx gene_name
0              0  overexpress     17525  HIST1H1C
1              0  overexpress     22532   MT-ND4L
2              0  overexpress     21868      MED6
3              0  overexpress     10147     BLVRB
4              0  overexpress     10117       BID

## 4) Model Setup

The Geneformer v2.0 base pretrained model (`gf-12L-38M-i4096`) is used, following the official example usage provided in the Geneformer model documentation. The same model weights and configuration are used across all experiments to ensure performance differences arise solely from inference strategy.


In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"

MODEL_NAME = "gf-12L-38M-i4096"
BATCH_SIZE = 8

cfg = GeneformerConfig(
    model_name=MODEL_NAME,
    batch_size=BATCH_SIZE,
    device=device,
)

geneformer = Geneformer(cfg)

print("Device:", device)
print("Model:", MODEL_NAME)
print("Batch size:", BATCH_SIZE)

INFO:helical.utils.downloader:Downloading 'geneformer/v2/gene_median_dictionary.pkl'
2026-01-13 16:02:38,745 - INFO:helical.utils.downloader:Downloading 'geneformer/v2/gene_median_dictionary.pkl'
INFO:helical.utils.downloader:Starting to download: 'https://helicalpackage.s3.eu-west-2.amazonaws.com/geneformer/v2/gene_median_dictionary.pkl'
2026-01-13 16:02:38,749 - INFO:helical.utils.downloader:Starting to download: 'https://helicalpackage.s3.eu-west-2.amazonaws.com/geneformer/v2/gene_median_dictionary.pkl'
gene_median_dictionary.pkl: 100%|██████████| 1.51M/1.51M [00:00<00:00, 2.36MB/s]
INFO:helical.utils.downloader:File saved to: '/root/.cache/helical/models/geneformer/v2/gene_median_dictionary.pkl'
2026-01-13 16:02:40,065 - INFO:helical.utils.downloader:File saved to: '/root/.cache/helical/models/geneformer/v2/gene_median_dictionary.pkl'
INFO:helical.utils.downloader:Downloading 'geneformer/v2/token_dictionary.pkl'
2026-01-13 16:02:40,069 - INFO:helical.utils.downloader:Downloading 'g

Device: cuda
Model: gf-12L-38M-i4096
Batch size: 8


## 5) Benchmarking Utilities (Runtime & Memory)


To ensure consistent and fair comparisons, benchmarking utilities are defined to measure:
* total inference runtime
* throughput (perturbations per second)
* CPU memory usage and peak GPU memory (via PyTorch)

These utilities are reused across all inference methods so that performance differences are directly comparable.

Peak GPU memory is reported via PyTorch and reflects the maximum allocation during inference, rather than total device usage.

In [ ]:
process = psutil.Process(os.getpid())

def cpu_mem_mb() -> float:
    """Return current CPU memory usage (MB)."""
    return process.memory_info().rss / (1024**2)

def summarize_run(
    name: str,
    num_pert: int,
    runtime_s: float,
    cpu_before: float,
    cpu_after: float,
):
    """Print standardized runtime and memory metrics for one inference run."""
    print(f"{name}: {num_pert} perturbations")
    print(f"  total time: {runtime_s:.2f}s")
    print(f"  throughput: {num_pert / runtime_s:.2f} perturbs/sec")
    print(f"  CPU memory delta (MB): {cpu_after - cpu_before:.1f}")

    if torch.cuda.is_available():
        print(
            f"  torch.cuda.max_memory_allocated (MB): "
            f"{torch.cuda.max_memory_allocated() / 1024**2:.1f}"
        )
    return {
        "name": name,
        "num_pert": num_pert,
        "runtime_s": runtime_s,
        "throughput": num_pert / runtime_s,
        "cpu_delta_mb": cpu_after - cpu_before,
        "gpu_peak_mb": (
            torch.cuda.max_memory_allocated() / 1024**2
            if torch.cuda.is_available()
            else None
        ),
    }

def benchmark(name: str, num_pert: int, fn):
    """
    Run `fn()` -> (embeddings, metrics),
    and print consistent metrics.
    """
    if torch.cuda.is_available():
        torch.cuda.reset_peak_memory_stats()

    cpu_before = cpu_mem_mb()
    embeddings, runtime_s = fn()
    cpu_after = cpu_mem_mb()

    metrics = summarize_run(name, num_pert, runtime_s, cpu_before, cpu_after)
    return embeddings, metrics

## 6) Naive Baseline ISP Inference
As a baseline, inference is run one perturbation at a time in a Python loop. This approach is intentionally inefficient and serves as a reference point for evaluating optimized inference.

In [ ]:
def embed_naive(
    model,
    perturbed_adata: ad.AnnData,
    n_cells: int | None = None,
):
    """
    Naive baseline for in-silico perturbation inference.

    Runs inference in a loop, embedding one perturbed cell at a time.
    Returns embeddings and total runtime (seconds).
    """
    num_cells = perturbed_adata.n_obs if n_cells is None else min(n_cells, perturbed_adata.n_obs)

    start_time = time.perf_counter()
    embeddings_list = []

    for i in range(num_cells):
        single = perturbed_adata[i : i + 1].copy()
        ds = model.process_data(single)
        emb = model.get_embeddings(ds)

        if torch.is_tensor(emb):
            emb = emb.detach().cpu().numpy()
        emb = np.asarray(emb)
        if emb.ndim == 1:
            emb = emb[None, :]
        embeddings_list.append(emb)

    runtime_s = time.perf_counter() - start_time
    embeddings = np.vstack(embeddings_list)
    return embeddings, runtime_s


def save_embedding_sample(
    embeddings: np.ndarray,
    perturbed_adata: ad.AnnData,
    n_samples: int = 10,
    output_path: str = "sample_latents.csv",
):
    n_samples = min(n_samples, embeddings.shape[0])

    emb_cols = [f"z_{i}" for i in range(embeddings.shape[1])]
    embedding_df = pd.DataFrame(embeddings[:n_samples], columns=emb_cols)

    metadata_df = perturbed_adata.obs.iloc[:n_samples].reset_index(drop=True)

    output_df = pd.concat([metadata_df, embedding_df], axis=1)
    output_df.to_csv(output_path, index=False)

    print(f"Saved embedding sample to: {output_path}")
    return output_df

In [ ]:
# Run naive baseline inference
N_BASELINE = perturbed_adata.n_obs  # run on all perturbations

embeddings_baseline, m_baseline = benchmark(
    name="Naive baseline (per-cell loop)",
    num_pert=N_BASELINE,
    fn=lambda: embed_naive(
        model=geneformer,
        perturbed_adata=perturbed_adata,
        n_cells=N_BASELINE,
    ),
)

runtime_baseline = m_baseline["runtime_s"]

# Save a small sample of embeddings for later correctness validation
baseline_sample_df = save_embedding_sample(
    embeddings=embeddings_baseline,
    perturbed_adata=perturbed_adata,
    n_samples=10,
    output_path="baseline_latent_sample.csv",
)

baseline_sample_df.head()

INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:02:50,899 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.downloader:Downloading 'hsapiens_pybiomart.csv'
2026-01-13 16:02:50,964 - INFO:helical.utils.downloader:Downloading 'hsapiens_pybiomart.csv'
INFO:helical.utils.downloader:Starting to download: 'https://helicalpackage.s3.eu-west-2.amazonaws.com/hsapiens_pybiomart.csv'
2026-01-13 16:02:50,968 - INFO:helical.utils.downloader:Starting to download: 'https://helicalpackage.s3.eu-west-2.amazonaws.com/hsapiens_pybiomart.csv'
hsapiens_pybiomart.csv: 100%|██████████| 2.30M/2.30M [00:00<00:00, 3.02MB/s]
INFO:helical.utils.downloader:File saved to: '/root/.cache/helical/models/hsapiens_pybiomart.csv'
2026-01-13 16:02:52,396 - INFO:helical.utils.downloader:File saved to: '/root/.cache/helical/models/hsapiens_pybiomart.csv'
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:02:52,582 - I

  0%|          | 0/1 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:02:53,838 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:02:53,873 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:02:54,590 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 1 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:02:54,767 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 1 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_cou

  0%|          | 0/1 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:02:54,887 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:02:54,902 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:02:55,676 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 1 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:02:55,868 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 1 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_cou

...

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:05:23,565 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:05:23,576 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:05:24,141 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 1 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:05:24,247 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 1 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_cou

  0%|          | 0/1 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:05:24,309 - INFO:helical.models.geneformer.model:Finished getting embeddings.


Naive baseline (per-cell loop): 200 perturbations
  total time: 153.42s
  throughput: 1.30 perturbs/sec
  CPU memory delta (MB): 35.0
  torch.cuda.max_memory_allocated (MB): 289.8
Saved embedding sample to: baseline_latent_sample.csv


base_cell_idx perturbation  gene_idx gene_name       z_0       z_1  \
0              0     knockout     17525  HIST1H1C  0.499270  0.033903   
1              0     knockout     22532   MT-ND4L  0.492931  0.036380   
2              0     knockout     21868      MED6  0.512118  0.031088   
3              0     knockout     10147     BLVRB  0.519841  0.031482   
4              0     knockout     10117       BID  0.502567  0.028679   

        z_2       z_3       z_4       z_5  ...     z_502     z_503     z_504  \
0  0.291115  0.972376  0.014256  0.183306  ... -0.366178 -0.287415 -0.400415   
1  0.214626  0.941395 -0.020560  0.179779  ... -0.369585 -0.357581 -0.359003   
2  0.272391  0.967115  0.003309  0.180547  ... -0.368794 -0.287330 -0.393649   
3  0.258920  0.941395  0.004302  0.173232  ... -0.377328 -0.283668 -0.369059   
4  0.280428  0.970194  0.003705  0.187598  ... -0.366687 -0.287778 -0.395817   

      z_505     z_506     z_507     z_508     z_509     z_510     z_511  
0 -0.080048 -0.406422  1.333409  0.584929  0.057465  0.226406 -0.146318  
1 -0.085817 -0.420326  1.346566  0.650430  0.048085  0.229814 -0.109983  
2 -0.085539 -0.412781  1.359824  0.593327  0.023671  0.215705 -0.151406  
3 -0.085145 -0.405839  1.350251  0.603045  0.010393  0.203036 -0.147533  
4 -0.087937 -0.419415  1.346210  0.573668  0.041623  0.216887 -0.151542  

[5 rows x 516 columns]

## 7) Optimized ISP Inference: Batching
Batching processes multiple perturbed cells in a single forward pass, which reduces Python loop overhead and allows the GPU to operate more efficiently, without changing the resulting embeddings.


In [ ]:
def embed_batched(
    model,
    perturbed_adata: ad.AnnData,
    batch_size: int = 32,
    n_cells: int | None = None,
):
    """
    Batched inference for ISP (embeds perturbed cells in batches).
    Returns embeddings and total runtime (seconds).
    """
    num_cells = perturbed_adata.n_obs if n_cells is None else min(n_cells, perturbed_adata.n_obs)

    start_time = time.perf_counter()
    embedding_batches = []

    for start in range(0, num_cells, batch_size):
        end = min(start + batch_size, num_cells)
        batch = perturbed_adata[start:end].copy()

        ds = model.process_data(batch)
        emb = model.get_embeddings(ds)

        if torch.is_tensor(emb):
            emb = emb.detach().cpu().numpy()
        emb = np.asarray(emb)
        if emb.ndim == 1:
            emb = emb[None, :]
        embedding_batches.append(emb)

    runtime_s = time.perf_counter() - start_time
    embeddings = np.vstack(embedding_batches)
    return embeddings, runtime_s


In [ ]:

BATCH_SIZE = 32
embeddings_b32, m_b32 = benchmark(
    name=f"Batched inference (batch_size={BATCH_SIZE})",
    num_pert=perturbed_adata.n_obs,
    fn=lambda: embed_batched(geneformer, perturbed_adata, batch_size=BATCH_SIZE),
)
print("Speedup vs naive:", runtime_baseline / m_b32["runtime_s"])

INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:05:24,391 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:05:24,996 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 32 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:05:25,118 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 32 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
INFO:helical.models.ge

  0%|          | 0/4 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:05:25,678 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:05:25,698 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:05:26,316 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 32 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:05:26,414 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 32 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_c

  0%|          | 0/4 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:05:26,766 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:05:26,781 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:05:27,323 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 32 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:05:27,424 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 32 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_c

...

  0%|          | 0/4 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:05:30,747 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:05:30,759 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:05:31,303 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 8 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:05:31,382 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 8 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_cou

  0%|          | 0/1 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:05:31,494 - INFO:helical.models.geneformer.model:Finished getting embeddings.


Batched inference (batch_size=32): 200 perturbations
  total time: 7.12s
  throughput: 28.11 perturbs/sec
  CPU memory delta (MB): 2.0
  torch.cuda.max_memory_allocated (MB): 761.4
Speedup vs naive: 21.561008090441767


Batch sizes are sweeped to characterize the throughput–batch-size tradeoff.



In [ ]:
# Sweep batch sizes
results = []
num_cells = perturbed_adata.n_obs

for batch_size in [4, 8, 16, 32, 64, 128]:
    _, metrics = benchmark(
        name=f"Sweep batched (batch_size={batch_size})",
        num_pert=num_cells,
        fn=lambda bs=batch_size: embed_batched(
            geneformer,
            perturbed_adata,
            batch_size=bs,
        ),
    )

    results.append({
        "method": "batched",
        "batch_size": batch_size,
        **metrics,
        "speedup_vs_naive": runtime_baseline / metrics["runtime_s"],
    })

INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:29:14,964 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:29:15,540 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 4 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:29:15,618 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 4 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
INFO:helical.models.gene

  0%|          | 0/1 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:29:15,742 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:29:15,752 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:29:16,296 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 4 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:29:16,373 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 4 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_cou

  0%|          | 0/1 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:29:16,493 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:29:16,503 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:29:17,136 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 4 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:29:17,261 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 4 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_cou

...

  0%|          | 0/16 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:30:43,512 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:30:43,531 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:30:44,094 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 72 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:30:44,178 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 72 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_c

  0%|          | 0/9 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:30:44,978 - INFO:helical.models.geneformer.model:Finished getting embeddings.


Sweep batched (batch_size=128): 200 perturbations
  total time: 3.55s
  throughput: 56.28 perturbs/sec
  CPU memory delta (MB): 0.0
  torch.cuda.max_memory_allocated (MB): 760.9


In [ ]:
# Display sweep results (sorted by runtime)
df_batched = pd.DataFrame(results).sort_values("runtime_s")
cols = ["batch_size", "runtime_s", "throughput", "gpu_peak_mb", "speedup_vs_naive"]
df_batched_display = df_batched[cols]
df_batched_display

batch_size  runtime_s  throughput  gpu_peak_mb  speedup_vs_naive
5         128   3.507625   57.018642   760.901367         43.739399
4          64   4.948298   40.417942   760.901367         31.004886
3          32   6.944893   28.798141   760.901367         22.091255
2          16  12.040599   16.610470   760.901367         12.742008
1           8  20.569646    9.723065   760.901367          7.458631
0           4  39.703091    5.037391   492.668457          3.864218

In [ ]:
best_batch_size = int(df_batched.iloc[0]["batch_size"])
print("Best batch size:", best_batch_size)

Best batch size: 128


Throughput increases steadily with batch size, reaching its maximum at batch_size = 128, where inference is ~44× faster than the naive baseline, with higher GPU memory usage reflecting increased parallelism.


## 8) Correctness Validation (baseline vs best batched inference)

To ensure batching does not change model outputs, embeddings are compared from the best batched configuration against the naive per-cell baseline. Maximum absolute difference and cosine similarity between corresponding embeddings are reported.


In [ ]:
# Run best batched inference
emb_best, m_best = benchmark(
    name=f"Best batched (batch_size={best_batch_size})",
    num_pert=perturbed_adata.n_obs,
    fn=lambda: embed_batched(geneformer, perturbed_adata, batch_size=best_batch_size),
)

assert perturbed_adata.n_obs == embeddings_baseline.shape[0]
assert embeddings_baseline.shape == emb_best.shape

max_abs_diff = float(np.max(np.abs(embeddings_baseline - emb_best)))

baseline_norm = embeddings_baseline / (np.linalg.norm(embeddings_baseline, axis=1, keepdims=True) + 1e-12)
best_norm = emb_best / (np.linalg.norm(emb_best, axis=1, keepdims=True) + 1e-12)
cos_sims = np.sum(baseline_norm * best_norm, axis=1)

print("Correctness vs baseline:")
print("  Max absolute difference:", max_abs_diff)
print("  Cosine similarity: mean =", float(cos_sims.mean()), "min =", float(cos_sims.min()))

INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:11:47,421 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:11:47,986 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 128 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:11:48,067 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 128 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
INFO:helical.models.

  0%|          | 0/16 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:11:49,523 - INFO:helical.models.geneformer.model:Finished getting embeddings.
INFO:helical.models.geneformer.model:Processing data for Geneformer.
2026-01-13 16:11:49,538 - INFO:helical.models.geneformer.model:Processing data for Geneformer.
INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
2026-01-13 16:11:50,069 - INFO:helical.utils.mapping:Mapped 20969 / 37318 genes to Ensembl IDs.
INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 72 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_counts'
    var: 'gene_name', 'index', 'ensembl_id', 'ensembl_id_collapsed' has no column attribute 'filter_pass'; tokenizing all cells.
2026-01-13 16:11:50,144 - INFO:helical.models.geneformer.geneformer_tokenizer:AnnData object with n_obs × n_vars = 72 × 37318
    obs: 'base_cell_idx', 'perturbation', 'gene_idx', 'gene_name', 'total_c

  0%|          | 0/9 [00:00<?, ?it/s]

INFO:helical.models.geneformer.model:Finished getting embeddings.
2026-01-13 16:11:50,918 - INFO:helical.models.geneformer.model:Finished getting embeddings.


Best batched (batch_size=128): 200 perturbations
  total time: 3.52s
  throughput: 56.81 perturbs/sec
  CPU memory delta (MB): 0.0
  torch.cuda.max_memory_allocated (MB): 760.9
Correctness vs baseline:
  Max absolute difference: 0.0
  Cosine similarity: mean = 1.0 min = 0.9999998211860657


The near-zero maximum absolute difference and cosine similarity ≈ 1 confirm that batching does not alter the Geneformer embeddings.


## 9) Performance Results
The table below summarizes baseline vs optimized performance using runtime, throughput, and peak GPU memory.

In [ ]:
# Final summary table (baseline vs best batched)
summary_rows = []

# Baseline row
summary_rows.append({
    "method": "naive",
    "batch_size": 1,
    "runtime_s": m_baseline["runtime_s"],
    "throughput": m_baseline["throughput"],
    "gpu_peak_mb": m_baseline["gpu_peak_mb"],
    "speedup_vs_naive": 1.0,
})

# Best batched row
summary_rows.append({
    "method": "batched (best)",
    "batch_size": best_batch_size,
    "runtime_s": m_best["runtime_s"],
    "throughput": m_best["throughput"],
    "gpu_peak_mb": m_best["gpu_peak_mb"],
    "speedup_vs_naive": m_baseline["runtime_s"] / m_best["runtime_s"],
})

df_summary = pd.DataFrame(summary_rows)

# Pretty formatting (optional)
df_summary = df_summary.sort_values("runtime_s")
df_summary


method  batch_size   runtime_s  throughput  gpu_peak_mb  \
1  batched (best)         128    3.520510   56.809943   760.901367   
0           naive           1  153.421399    1.303599   289.818848   

   speedup_vs_naive  
1         43.579305  
0          1.000000

## Final Results & Takeaways

Batching reduces inference time by lowering the per-perturbation cost of preprocessing and Python control flow, allowing many cells to be embedded simultaneously, and more effectively utilizing GPU parallelism.

### On 200 single-gene knockout perturbations

- **Naive per-cell inference:** 153.42 s (1.30 perturbations/sec), peak GPU allocation ≈ 289.8 MB  
- **Best batched inference (batch_size = 128):** 3.52 s (56.81 perturbations/sec), peak GPU allocation ≈ 760.9 MB  
- **Overall speedup:** **43.6×** relative to the naive baseline  

### Key takeaways

- A batch size of 128 provides the best performance on this hardware, achieving a large speedup at the cost of increased but manageable GPU memory usage.
- Correctness validation confirms that batching preserves Geneformer embeddings up to floating-point precision, indicating no change in model behavior.